In [1]:
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import string
import re
import random

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [2]:
lines = open('data/eng-fra.txt', encoding='utf-8').read().strip().split('\n')

In [3]:
lines

['Go.\tVa !',
 'Run!\tCours\u202f!',
 'Run!\tCourez\u202f!',
 'Wow!\tÇa alors\u202f!',
 'Fire!\tAu feu !',
 "Help!\tÀ l'aide\u202f!",
 'Jump.\tSaute.',
 'Stop!\tÇa suffit\u202f!',
 'Stop!\tStop\u202f!',
 'Stop!\tArrête-toi !',
 'Wait!\tAttends !',
 'Wait!\tAttendez !',
 'I see.\tJe comprends.',
 "I try.\tJ'essaye.",
 "I won!\tJ'ai gagné !",
 "I won!\tJe l'ai emporté !",
 'Oh no!\tOh non !',
 'Attack!\tAttaque !',
 'Attack!\tAttaquez !',
 'Cheers!\tSanté !',
 'Cheers!\tÀ votre santé !',
 'Cheers!\tMerci !',
 'Get up.\tLève-toi.',
 "Got it!\tJ'ai pigé !",
 'Got it!\tCompris !',
 'Got it?\tPigé\u202f?',
 'Got it?\tCompris\u202f?',
 "Got it?\tT'as capté\u202f?",
 'Hop in.\tMonte.',
 'Hop in.\tMontez.',
 'Hug me.\tSerre-moi dans tes bras !',
 'Hug me.\tSerrez-moi dans vos bras !',
 'I fell.\tJe suis tombée.',
 'I fell.\tJe suis tombé.',
 'I know.\tJe sais.',
 'I left.\tJe suis parti.',
 'I left.\tJe suis partie.',
 "I lost.\tJ'ai perdu.",
 "I'm 19.\tJ'ai 19 ans.",
 "I'm OK.\tJe vais bien.",

In [4]:
# Turn a Unicode string to plain ASCII, thanks to
# https://stackoverflow.com/a/518232/2809427
def unicodeToAscii(s):
    return ''.join(
        c for c in unicodedata.normalize('NFD', s)
        if unicodedata.category(c) != 'Mn'
    )

# Lowercase, trim, and remove non-letter characters


def normalizeString(s):
    s = unicodeToAscii(s.lower().strip())
    s = re.sub(r"([.!?])", r" \1", s)
    s = re.sub(r"[^a-zA-Z.!?]+", r" ", s)
    return s

In [5]:
pairs = [[normalizeString(s) for s in l.split('\t')] for l in lines]

In [6]:
pairs

[['go .', 'va !'],
 ['run !', 'cours !'],
 ['run !', 'courez !'],
 ['wow !', 'ca alors !'],
 ['fire !', 'au feu !'],
 ['help !', 'a l aide !'],
 ['jump .', 'saute .'],
 ['stop !', 'ca suffit !'],
 ['stop !', 'stop !'],
 ['stop !', 'arrete toi !'],
 ['wait !', 'attends !'],
 ['wait !', 'attendez !'],
 ['i see .', 'je comprends .'],
 ['i try .', 'j essaye .'],
 ['i won !', 'j ai gagne !'],
 ['i won !', 'je l ai emporte !'],
 ['oh no !', 'oh non !'],
 ['attack !', 'attaque !'],
 ['attack !', 'attaquez !'],
 ['cheers !', 'sante !'],
 ['cheers !', 'a votre sante !'],
 ['cheers !', 'merci !'],
 ['get up .', 'leve toi .'],
 ['got it !', 'j ai pige !'],
 ['got it !', 'compris !'],
 ['got it ?', 'pige ?'],
 ['got it ?', 'compris ?'],
 ['got it ?', 't as capte ?'],
 ['hop in .', 'monte .'],
 ['hop in .', 'montez .'],
 ['hug me .', 'serre moi dans tes bras !'],
 ['hug me .', 'serrez moi dans vos bras !'],
 ['i fell .', 'je suis tombee .'],
 ['i fell .', 'je suis tombe .'],
 ['i know .', 'je sais 

In [7]:
lines = open('without_pos_tags/English', encoding='utf-8').read().strip().split('\n')

In [8]:
lines

['Fresh breath and shining teeth enhance your personality .',
 'Your self-confidence also increases with teeth .',
 'Bacteria stay between our gums and teeth .',
 'They make teeth dirty and breath stinky .',
 'You may keep your teeth clean and breath fresh by the help of some easy tips given here .',
 'Clean your teeth properly .',
 'It takes two to three minutes to clean your teeth properly .',
 'But most of the people give less than one minute for this .',
 'Drink plenty of water .',
 'Bacteria attack fast if the mouth dries up .',
 'With this stink comes from breath .',
 'By drinking plenty of water not only the left-over pieces of food gets cleaned but saliva also gets formed .',
 'Saliva has important role in keeping the mouth clean .',
 'Saliva destroys those bacteria which create stink in breath .',
 'Chew the sugar-free chewing gum .',
 'Saliva is formed by chewing the chewing gum .',
 'Chewing gum helps in keeping the teeth clean .',
 'Sugared chewing gum is not supposed to be

In [9]:
lines1 = open('without_pos_tags/Hindi', encoding='utf-8').read().strip().split('\n')
lines1

['ताजा साँसें और चमचमाते दाँत आपके व्यक्तित्व को निखारते हैं ।',
 'दाँतों से आपका आत्मविश्\u200dवास भी बढ़ता है ।',
 'हमारे मसूढ़ों और दाँतों के बीच बैक्टीरिया मौजूद होते हैं ।',
 'ये दाँतों को गंदा और साँसों को बदबूदार बना देते हैं ।',
 'यहाँ दिए कुछ आसान नुस्खों की मदद से आप अपने दाँतों को स्वच्छ और साँसों को ताजा रख सकते हैं  ।',
 'दाँतों को ठीक से साफ करें ।',
 'दाँतों को ठीक से साफ करने में दो से तीन मिनट का समय लगता है ।',
 'लेकिन ज्यादातर लोग इसके लिए एक मिनट से भी कम समय देते हैं ।',
 'खूब पानी पीएँ ।',
 'मुँह सूखने पर बैक्टीरिया हमला तेज कर देते हैं ।',
 'इससे साँसों से बदबू आने लगती है ।',
 'खूब पानी पीने से न केवल खाने के बचे - खुचे टुकड़े साफ हो जाते हैं , बल्कि लार भी बनती है ।',
 'मुँह साफ रखने में लार की खास भूमिका होती है ।',
 'लार उन बैक्टीरिया को नष्ट करती है जो साँसों में बदबू पैदा करते हैं ।',
 'चबाएँ शुगर रहित चुइंग गम ।',
 'चुइंग गम चबाने से लार बनती है ।',
 'चुइंग गम से दाँतों को साफ रखने में मदद मिलती है ।',
 'शुगर युक्त गम को सेहत के लिए अच्छा नहीं माना जाता ।'

In [10]:
len(lines)

49999

In [11]:
len(lines1)

49999

In [12]:
ans_list = []

for i in range(len(lines)):
    a = lines[i] + "\t" + lines1[i]
    print (a)
    ans_list.append(a)

Fresh breath and shining teeth enhance your personality .	ताजा साँसें और चमचमाते दाँत आपके व्यक्तित्व को निखारते हैं ।
Your self-confidence also increases with teeth .	दाँतों से आपका आत्मविश्‍वास भी बढ़ता है ।
Bacteria stay between our gums and teeth .	हमारे मसूढ़ों और दाँतों के बीच बैक्टीरिया मौजूद होते हैं ।
They make teeth dirty and breath stinky .	ये दाँतों को गंदा और साँसों को बदबूदार बना देते हैं ।
You may keep your teeth clean and breath fresh by the help of some easy tips given here .	यहाँ दिए कुछ आसान नुस्खों की मदद से आप अपने दाँतों को स्वच्छ और साँसों को ताजा रख सकते हैं  ।
Clean your teeth properly .	दाँतों को ठीक से साफ करें ।
It takes two to three minutes to clean your teeth properly .	दाँतों को ठीक से साफ करने में दो से तीन मिनट का समय लगता है ।
But most of the people give less than one minute for this .	लेकिन ज्यादातर लोग इसके लिए एक मिनट से भी कम समय देते हैं ।
Drink plenty of water .	खूब पानी पीएँ ।
Bacteria attack fast if the mouth dries up .	मुँह सूखने पर बैक्टीरिया

These forms are called cyst and ova .	एंटामीबा दो रूपों में शरीर की वृहत् आंत्र में विद्यमान रहता है ।
Humans takes it inside the body in the form of cyst through food items and beverages .	इन रूपों को पुटी ( cyst ) और अंडाणु ( ova ) कहते हैं ।
This cyst sometimes takes the form of eggs on entering the large intestine .	मनुष्य खाद्य एवं पेय पदार्थो  द्वारा इस जीवाणु को पुटी रूप में शरीर के अंदर ग्रहण करता है ।
Among the main symptoms of dysentery patient has diarrhoea along with an acute form of stomach ache and an acute convulsion occurs near the anus .	यह पुटी कभी-कभी बृहत् आंत्र में पहुँचकर अडाणु का रूप ग्रहण कर लेती है ।
On diagnosing such patients a tenderness is found in caecum and the left iliac region and some fever also occurs .	`` पेचिश के मुख्य लक्षणों में रोगी को तीव्र स्वरूप के उदरशूल के साथ अतिसार होता है तथा गुदा के पास के भाग में तीव्र ऐंठन होती है । ``
Flies are extremely helpful in spreading dysentery .	ऐसे रोगियों की परीक्षा करने पर अंधनाल ( caecum ) तथा वाम श्रोणीय 

Till date surgery was the only treatment to take out the stone but several complications used to crop up in that .	अभी तक पथरी को निकालने के लिए शल्यक्रिया ही एक मात्र उपचार था , मगर उस में अनेक कठिनाइयाँ भी सामने आती थीं ।
But now a technique which is called lithoptysis has become available to take the stone out without surgery .	मगर अब पथरी को ऑपरेशन के बिना निकालने की विधि उपलब्ध हो गई है जिसे लीथोट्रिप्स कहा जाता है ।
The technique of lithoptysis was used in 1980 for the first time and from 1987 it has become available in India as well .	लीथोट्रिप्स विधि का सर्वप्रथम उपयोग 1980 में किया गया और 1987 से यह विधि भारत में भी उपलब्ध है ।
In the lithoptysis technique the stones present in any part of the urinary tract are targeted with aim and then the stones are broken by the shower of high capacity waves .	लीथोट्रिप्स विधि में मूत्रमार्ग के किसी भी हिस्से में मौजूद पथरी की अचूक निशानदेही की जाती है और फिर उस पर अति क्षमता वाली तरंगों की बौछार पथरी को तोड़ दिया जाता है ।
The pieces of st

Monsoon depression is produced due to the effect of weather .	मानसून डिप्रेशन मौसम के प्रभाव के कारण पैदा होता है ।
Because there is more dampness in the monsoon season , body is always sort of sticky , on top of that there is less electricity as well , by which the melatonin hormone is produced less in body , which gives rise to depression .	चूँकि मानसून के मौसम में आर्द्रता ज्यादा होती है , शरीर हमेशा चिपचिपा सा रहता है , ऊपर से बिजली की कमी भी हो जाती है , जिससे मस्तिष्क में मेलाटोनिन हार्मोन कम बनता है , जो डिप्रेशन को जन्म देता है ।
Because of monsoon depression we do n't like anything .	मानसून डिप्रेशन के कारण कुछ भी अच्छा नहीं लगता ।
During monsoon we do n't even feel like doing our favorite things .	मानसून डिप्रेशन के कारण मनमोहक काम करने की भी इच्छा नहीं होती ।
Due to monsoon depression temper flies at everything and irritability is felt .	मानसून डिप्रेशन के कारण बात - बात में गुस्सा आना और चिड़चिड़ापन होता है ।
Due to monsoon depression we feel sort of tired .	मानसून डिप्रेशन

In this the person comes out of the bed and also starts climbing up some stairs gradually and at the end he comes back .	इसमें व्यक्‍ति बिस्तर से बाहर आ जाता है और धीरे-धीरे कुछ सीढ़ियाँ भी चढ़ सकता है और अंत में वह वापस आ सकता है ।
The complete effort of the doctor is this that once again the patient becomes a healthy and active citizen of the society .	चिकित्सक का पूरा प्रयास यही रहता है कि रोगी फिर से सामाज का एक स्वस्थ और सक्रिय नागरिक बने ।
In the third stage it is tried to make the patient physically and mentally completely healthy .	तीसरे चरण में रोगी को शारीरिक और मानसिक रूप से पूर्ण स्वस्थ बनाने का प्रयास किया जाता है ।
In the SAAOL natural medication keep the heart disease free .	साओल प्राकृतिक चिकित्सा से दिल को रखें रोगमुक्‍त -
Today the number of heart patients is increasing at a fast pace .	आज हृदय रोगियों की संख्या तीव्र गति से बढ़ रही है ।
Medical science has also gone very far in this direction .	चिकित्सा विज्ञान भी इस दिशा में काफी आगे पहुँच रहा है ।
With techniques l

...

Its nautral beauty is peculiarly wondrous .	इसका प्राकृतिक सौंदर्य अपने आप में अनोखा है ।
Lakhs of tourists visit Philipipines evey year to see it .	इसे देखने लाखों सैलानी प्रतिवर्ष फिलीपिंस पहुँचते हैं ।
This is in the Bohol region of Philippines .	यह फिलीपिंस के बोहोल प्रांत में है ।
A total of 1776 hills are included in the Chocolatey Hills .	चॉकलेटी हिल्स में कुल 1776 पहाड़ियाँ शामिल है ।
These hills are spread over an area of 50 square kilometers .	ये पहाड़ियाँ 50 वर्ग किलोमीटर के दायरे में फैली हैं ।
This has got the status of the third National Monument of Philippines .	इसे फिलीपिंस में तीसरे राष्‍ट्रीय स्मारक का दर्जा मिला ।
This is prominently included in the World Heritage list of UNESCO .	यूनोस्को की वर्ल्ड हेरिटेज सूची में यह प्रमुखता से शामिल है ।
These hill do not remain of the chocolatey tone the whole year .	ये पहाड़ियाँ साल भर चॉकलेटी रंगत की नहीं रहती ।
Actually on ordinary days there is green grass spread on these hills but as soon as the summers come that is after Apri

There are temples of Hanumanji all around the Ramraja temple .	रामराजा मंदिर के चारों तरफ हनुमान जी के मंदिर हैं ।
Temples of Chhadadari Hanuman , Hanuman of Bajaria , Lanka Hanuman are all around in the form of security circle .	छडदारी हनुमान , बजरिया के हनुमान , लंका हनुमान के मंदिर एक सुरक्षा चक्र के रूप में चारों तरफ हैं ।
Among other precious heritages of Orccha Laxmi Temple , Panchamukhi Mahadeo , Radhika Bihari Temple , Rajamahal , Raipravin Mahal , Hall of Hardaul , Monument of Hardaul , Jehangir Mahal and its paintings are major .	`` ओरछा की अन्य बहुमूल्य धरोहरों में लक्ष्मी मंदिर , पंचमुखी महादेव , राधिका बिहारी मंदिर , राजामहल , रायप्रवीण महल , हरदौल की बैठक , हरदौल की समाधि , जहाँगीर महल और उसकी चित्रकारी प्रमुख हैं ।
Orccha is at a distance of merely 15 kms from Jhansi .	ओरछा झाँसी से मात्र 15 कि.मी. की दूरी पर है ।
Jhansi is connected with major railway lines of the country .	झाँसी देश की प्रमुख रेलवे लाइनों से जुड़ा है ।
Grand residential houses are built for tourists in 

Once came the turn of the grandson of an old lady in a Khap but that lady refused to sacrifice her grandson .	एक बार एक खाप की बूढी महिला के पोते की बारी आई लेकिन महिला ने अपने पोते की बलि देने से इंकार कर दिया ।
So that the Goddess does not turn wrathful , thinking this the villagers decided that by playing Bagwaal which means a thrilling game of stones continuously blood should be shed from one human body .	कहीं देवी कुपित न हो जाए , यह सोचकर गाँव वालों ने निर्णय लिया कि बगवाल खेलकर यानी पत्थरों का रोमांचकारी खेल खेलकर एक मनुष्य शरीर के बराबर रक्त बहाया जाए ।
Since then as the symbolic protest of human sacrifice keeping this tradition alive on the day of Raksha Bandhan the people of all the four Khaps reach here with drums and barrels and play the thrilling game of stones .	तभी से नरबलि के प्रतीकात्मक विरोध स्वरूप इस परंपरा को जीवित रखते हुए हर साल रक्षाबंधन के दिन चारों खापों के लोग यहाँ ढोल नगाड़ों के साथ पहुँचते हैं और पत्थरों के रोमांचकारी खेल को खेलते हैं ।
Warriors of all the fo

From Chajpur to Talra is called the mountain of moonlit night because in these when the rays of sun fall then a sight like that of moonlit night forms .	छाजपुर से लेकर तालरा तक को चाँदनी रात के पहाड़ कहा जाता है क्योंकि इनमें जब सूर्य की किरणें पड़ती हैं तब चाँदनी रात जैसा दृश्य बनता है ।
The sight here on moonlit nights is not lesser than any heaven .	चाँदनी रात में यहाँ का नजारा किसी स्वर्ग से कम नहीं होता है ।
Gurhad is a beautiful village based in the middle of dense forests at a distance of 8 k . . from Tharoch , which is an extremely popular village for its unparalled beauty and natural grandeur .	गुरहाड़ थरोच से 8 कि.मी. की दूरी पर घने जंगलों के बीच बसा सुंदर गाँव है , जो अपने अनुपम सौंदर्य एवं प्राकृतिक वैभव के लिए अत्यंत लोकप्रिय गाँव है ।
Here shepherds and goatherds are local residents who do the business of sheep and goats .	यहाँ पर भेड़ियाले एवं बकराले ( भेड़ एवं बकरियाँ चराने वाले ) स्थानीय निवासी हैं जो भेड़ - बकरियों का व्यापार करते हैं ।
These people make and sell sweaters 

In Kaladhungi there is museum of Jim Corbett Sahib where some important things related to his private life are kept .	कालाढुंगी में जिम कार्बेट साहब का म्यूजियम है , जहाँ उनकी निजी जिंदगी से जुड़ी कुछ अहम चीजें रखी हैं ।
It struck half past twelve while returning back .	लौटते-लौटते साढ़े बारह बज गए ।
Kaladhungi is an extremely beautiful place , Jim Corbett settled in this place only .	कालाढुंगी बेहद खूबसूरत जगह है , जिम कार्बेट इसी गाँब में आकर बसे थे ।
On reaching Resort safari gypsy was waiting for us .	रिजॉर्ट पहुँचने पर सफारी जिप्सी हमारा इंतजार कर रही थी ।
It was told that facility of siting was done in number one site Bijraani there .	बताया गया कि उन्होंने वहाँ की नंबर एक साइट बिजरानी में साइटिंग की व्यवस्था कराई है ।
On asking about number one we were told that grassland are more there and during this time tiger come that side only to escape from cold .	नंबर एक के बारे में पूछने पर बताया कि वहाँ ग्रासलैंड ज्यादा है और टाइगर इस दौरान ठंड से बचने के लिए उसी तरफ आते हैं ।
We were giv

In [13]:
ans_list

['Fresh breath and shining teeth enhance your personality .\tताजा साँसें और चमचमाते दाँत आपके व्यक्तित्व को निखारते हैं ।',
 'Your self-confidence also increases with teeth .\tदाँतों से आपका आत्मविश्\u200dवास भी बढ़ता है ।',
 'Bacteria stay between our gums and teeth .\tहमारे मसूढ़ों और दाँतों के बीच बैक्टीरिया मौजूद होते हैं ।',
 'They make teeth dirty and breath stinky .\tये दाँतों को गंदा और साँसों को बदबूदार बना देते हैं ।',
 'You may keep your teeth clean and breath fresh by the help of some easy tips given here .\tयहाँ दिए कुछ आसान नुस्खों की मदद से आप अपने दाँतों को स्वच्छ और साँसों को ताजा रख सकते हैं  ।',
 'Clean your teeth properly .\tदाँतों को ठीक से साफ करें ।',
 'It takes two to three minutes to clean your teeth properly .\tदाँतों को ठीक से साफ करने में दो से तीन मिनट का समय लगता है ।',
 'But most of the people give less than one minute for this .\tलेकिन ज्यादातर लोग इसके लिए एक मिनट से भी कम समय देते हैं ।',
 'Drink plenty of water .\tखूब पानी पीएँ ।',
 'Bacteria attack f

In [ ]:
print ("Hello World" + "\t" + "blue book")

In [14]:
with open('eng_hindi.txt', 'w') as f:
    for item in ans_list:
        f.write("%s\n" % item)